In [1]:
import torch
import torch.nn as nn
import torch.nn.functional as F
import matplotlib.pyplot as plt
import seaborn as sns
import numpy as np
import dgl
from dgl.nn import ChebConv
import networkx as nx
import networkx.algorithms.community as nx_comm
import numpy as np
import pandas as pd
import numpy.linalg as alg

import os
from tqdm import tqdm
from functools import reduce
import argparse


def node_connects_cluster(node):
    return set(map(lambda x: inverse_cluster_dict[x], list(g[node]))).union(set([inverse_cluster_dict[node]]))


def po_linear_model(graph, alpha=1, beta=1, sigma=0.1, gamma=2):    
    for i in graph.nodes:
        graph.nodes[i]["y"] = alpha + beta * graph.nodes[i]["z"] + sigma * np.random.normal() +  gamma * sum([graph.nodes[ngbr]['z'] for ngbr in graph[i]])/graph.degree[i]  

def po_multiplicative_model(graph, alpha=1, sigma=0.1, delta=1, gamma=2): 
    for i in graph.nodes:
        graph.nodes[i]["y"] = ( (alpha + sigma * np.random.normal()) * graph.degree[i]/avg_deg )  *  (1 + delta * graph.nodes[i]["z"] + gamma * sum([graph.nodes[ngbr]['z'] for ngbr in graph[i]]) / len(graph[i]) )

DGL backend not selected or invalid.  Assuming PyTorch for now.


Setting the default backend to "pytorch". You can change it in the ~/.dgl/config.json file or export the DGLBACKEND environment variable.  Valid options are: pytorch, mxnet, tensorflow (all lowercase)


/root/miniconda3/envs/myconda/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [2]:

path = 'Dataset/socfb-Stanford3.mtx'

df = pd.read_table(path, skiprows=1, names = ["source", "target"], sep=" ")
g = nx.from_pandas_edgelist(df)

# calculate basic elements
num_nodes = g.number_of_nodes()
num_edges = g.number_of_edges()
degs = [g.degree[i] for i in g.nodes]
avg_deg = sum(degs)/len(degs)

res = 10


# clustering
# generally, we fix the outcome of clustering
clusters = nx_comm.louvain_communities(g, seed = 10, resolution=res)
clusters = sorted(clusters, key = len, reverse=True)
cluster_sizes = list(map(len, clusters))
num_cluster = len(clusters)

# dict: from node to its cluster
inverse_cluster_dict = {
    node: cl for cl in range(num_cluster) for node in clusters[cl]
}

# dict: from node to its connected cluster
node_to_connected_clusters = {
    node: node_connects_cluster(node) for node in range(1, num_nodes + 1)
}


for i in g.nodes:
    g.nodes[i]["deg"] = g.degree[i]

rev_cluster_sizes = cluster_sizes[::-1]
rev_clusters = clusters[::-1]
rev_cluster_sizes = np.array(rev_cluster_sizes)


In [3]:
dgl_G = dgl.from_networkx(g)

In [4]:
ramps = [0.02, 0.05, 0.1, 0.25, 0.5]
repeat_num = 1000

In [5]:

class GCN(nn.Module):
    def __init__(self):
        super().__init__()
        self.conv1 = dgl.nn.ChebConv(2, 16, 2)
        self.conv2 = dgl.nn.ChebConv(16, 16, 1)
        self.conv3 = dgl.nn.ChebConv(16, 1, 1)
        
    def forward(self, g, features):
        x = self.conv1(g, features)
        x = self.conv2(g, x)
        x = self.conv3(g, x)
        return x
        

In [ ]:
# cluster-level ber

GATE_hat_list = np.zeros((repeat_num, len(ramps)))


for seed in tqdm(range(repeat_num)):
    
    np.random.seed(seed)     
        
    for num_step in range(len(ramps)): 
        # no ramp
        rollout_index = np.random.uniform(0, 1, size=(num_cluster,))           
        torch.manual_seed(2)
        p_list = ramps[num_step:]        
            
        print(f"Seed: {seed}")
        
        g_feat_list = []
        y_list = []
        
        for p in p_list:
            nx.set_node_attributes(g, 0, "z")            
            tr_clusters = np.arange(num_cluster)[rollout_index<p]
            if len(tr_clusters) > 0:
                tr_units = reduce(lambda x, y: x.union(y), [clusters[i] for i in tr_clusters])              
                nx.set_node_attributes(g, {unit:1 for unit in tr_units}, "z")
            
            po_linear_model(g, gamma = 1)            
            g_feat_list.append(torch.tensor([[g.nodes[n]['z'], g.nodes[n]['deg']] for n in g.nodes], dtype=torch.float))
            y_list.append(torch.tensor([[g.nodes[n]['y']] for n in g.nodes], dtype=torch.float).reshape(-1))
    
        # Instantiate the model and optimizer
        model = GCN()
        optimizer = torch.optim.Adam(model.parameters(), lr=0.004)
        
        # Train the model
        for epoch in range(400):
            for i in range(len(p_list)):
                model.train()
                optimizer.zero_grad()
                out = model(dgl_G, g_feat_list[i])
                loss = F.mse_loss(out.squeeze(), y_list[i])  
                loss.backward()
                optimizer.step()
            
                if epoch % 50 == 0:
                    print(f'Epoch {epoch}, Treat Prop: {p_list[i]:.2f}, Loss: {loss:.4f}')
    
        print(loss.item())
        g_feat = g_feat_list[0]
    
        g_feat[:,0] = 0
        global_control_pred = model(dgl_G, g_feat).detach().numpy()
    
        g_feat[:,0] = 1
        global_treat_pred = model(dgl_G, g_feat).detach().numpy()
    
        GATE_hat = global_treat_pred.mean() - global_control_pred.mean()
    
        GATE_hat_list[seed, num_step] = GATE_hat
        
    torch.save(GATE_hat_list, "Result/NoRamp_Ber_cluster_res10_final.pkl")


  0%|          | 0/1000 [00:00<?, ?it/s]

Seed: 0


/root/miniconda3/envs/myconda/lib/python3.10/site-packages/dgl/nn/pytorch/conv/chebconv.py:108: DGLWarning: lambda_max is not provided, using default value of 2.  Please use dgl.laplacian_lambda_max to compute the eigenvalues.
  dgl_warning(


Epoch 0, Treat Prop: 0.02, Loss: 8.0895
Epoch 0, Treat Prop: 0.05, Loss: 2.3997
Epoch 0, Treat Prop: 0.10, Loss: 1.2479
Epoch 0, Treat Prop: 0.25, Loss: 1.7940
Epoch 0, Treat Prop: 0.50, Loss: 3.0252
Epoch 50, Treat Prop: 0.02, Loss: 0.1049
Epoch 50, Treat Prop: 0.05, Loss: 0.1419
Epoch 50, Treat Prop: 0.10, Loss: 0.1246
Epoch 50, Treat Prop: 0.25, Loss: 0.2342
Epoch 50, Treat Prop: 0.50, Loss: 0.5803
Epoch 100, Treat Prop: 0.02, Loss: 0.0155
Epoch 100, Treat Prop: 0.05, Loss: 0.0201
Epoch 100, Treat Prop: 0.10, Loss: 0.0223
Epoch 100, Treat Prop: 0.25, Loss: 0.0341
Epoch 100, Treat Prop: 0.50, Loss: 0.0562
Epoch 150, Treat Prop: 0.02, Loss: 0.2140
Epoch 150, Treat Prop: 0.05, Loss: 0.1367
Epoch 150, Treat Prop: 0.10, Loss: 0.0381
Epoch 150, Treat Prop: 0.25, Loss: 0.2284
Epoch 150, Treat Prop: 0.50, Loss: 0.1226
Epoch 200, Treat Prop: 0.02, Loss: 0.0152
Epoch 200, Treat Prop: 0.05, Loss: 0.0173
Epoch 200, Treat Prop: 0.10, Loss: 0.0198
Epoch 200, Treat Prop: 0.25, Loss: 0.0308
Epoch 2

  0%|          | 1/1000 [00:32<9:02:59, 32.61s/it]

...

0.035179104655981064
Seed: 886
Epoch 0, Treat Prop: 0.02, Loss: 8.2232
Epoch 0, Treat Prop: 0.05, Loss: 2.6406
Epoch 0, Treat Prop: 0.10, Loss: 1.4838
Epoch 0, Treat Prop: 0.25, Loss: 2.1384
Epoch 0, Treat Prop: 0.50, Loss: 3.4183
Epoch 50, Treat Prop: 0.02, Loss: 0.1210
Epoch 50, Treat Prop: 0.05, Loss: 0.2176
Epoch 50, Treat Prop: 0.10, Loss: 0.0789
Epoch 50, Treat Prop: 0.25, Loss: 0.1617
Epoch 50, Treat Prop: 0.50, Loss: 0.2766
Epoch 100, Treat Prop: 0.02, Loss: 0.0431
Epoch 100, Treat Prop: 0.05, Loss: 0.0316
Epoch 100, Treat Prop: 0.10, Loss: 0.0371
Epoch 100, Treat Prop: 0.25, Loss: 0.0523
Epoch 100, Treat Prop: 0.50, Loss: 0.0491
Epoch 150, Treat Prop: 0.02, Loss: 0.0501
Epoch 150, Treat Prop: 0.05, Loss: 0.0343
Epoch 150, Treat Prop: 0.10, Loss: 0.0373
Epoch 150, Treat Prop: 0.25, Loss: 0.0618
Epoch 150, Treat Prop: 0.50, Loss: 0.0490
Epoch 200, Treat Prop: 0.02, Loss: 0.0443
Epoch 200, Treat Prop: 0.05, Loss: 0.0333
Epoch 200, Treat Prop: 0.10, Loss: 0.0345
Epoch 200, Treat P

 89%|████████▊ | 887/1000 [7:08:57<54:33, 28.97s/it]

0.031971801072359085
Seed: 887
Epoch 0, Treat Prop: 0.02, Loss: 8.0176
Epoch 0, Treat Prop: 0.05, Loss: 2.5383
Epoch 0, Treat Prop: 0.10, Loss: 1.2901
Epoch 0, Treat Prop: 0.25, Loss: 2.3167
Epoch 0, Treat Prop: 0.50, Loss: 3.8878
Epoch 50, Treat Prop: 0.02, Loss: 0.1394
Epoch 50, Treat Prop: 0.05, Loss: 0.1965
Epoch 50, Treat Prop: 0.10, Loss: 0.1562
Epoch 50, Treat Prop: 0.25, Loss: 0.2775
Epoch 50, Treat Prop: 0.50, Loss: 0.5646
Epoch 100, Treat Prop: 0.02, Loss: 0.0245
Epoch 100, Treat Prop: 0.05, Loss: 0.0263
Epoch 100, Treat Prop: 0.10, Loss: 0.0354
Epoch 100, Treat Prop: 0.25, Loss: 0.0450
Epoch 100, Treat Prop: 0.50, Loss: 0.0642
Epoch 150, Treat Prop: 0.02, Loss: 0.0149
Epoch 150, Treat Prop: 0.05, Loss: 0.0269
Epoch 150, Treat Prop: 0.10, Loss: 0.0205
Epoch 150, Treat Prop: 0.25, Loss: 0.0388
Epoch 150, Treat Prop: 0.50, Loss: 0.0521
Epoch 200, Treat Prop: 0.02, Loss: 0.0174
Epoch 200, Treat Prop: 0.05, Loss: 0.0521
Epoch 200, Treat Prop: 0.10, Loss: 0.0614
Epoch 200, Treat P

 89%|████████▉ | 888/1000 [7:09:26<54:13, 29.05s/it]

0.06264788657426834
Seed: 888
Epoch 0, Treat Prop: 0.02, Loss: 7.9930
Epoch 0, Treat Prop: 0.05, Loss: 2.3452
Epoch 0, Treat Prop: 0.10, Loss: 1.4119
Epoch 0, Treat Prop: 0.25, Loss: 2.4411
Epoch 0, Treat Prop: 0.50, Loss: 3.6558
